In [2]:
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from bs4 import BeautifulSoup
import pymysql
import csv

url = 'https://ifoodie.tw/'
response = requests.get(url)
soup = BeautifulSoup(response.text, 'html.parser')

In [4]:
# 取各類別網址
# 取網址絕對路徑 => 第一個 

target_hrefs_2 = []

outer_div = soup.find('div', class_='jsx-1638812939 category-block-item-outer')
links = outer_div.findAll('a')

total = 0
for link in links:
    href_2 = link.get('href')
    href_url = f'https://ifoodie.tw{href_2}'
    target_hrefs_2.append(href_url)
    total+=1
    
    if total == 10:
        break


print(target_hrefs_2)


['https://ifoodie.tw/explore/台北市/list/%E9%8D%8B%E9%A1%9E', 'https://ifoodie.tw/explore/台北市/list/%E6%97%A5%E5%BC%8F', 'https://ifoodie.tw/explore/台北市/list/%E7%87%92%E8%82%89', 'https://ifoodie.tw/explore/台北市/list/%E7%B2%BE%E7%B7%BB%E9%AB%98%E7%B4%9A', 'https://ifoodie.tw/explore/台北市/list/%E6%97%A9%E5%8D%88%E9%A4%90', 'https://ifoodie.tw/explore/台北市/list/%E7%94%9C%E9%BB%9E%E9%A1%9E', 'https://ifoodie.tw/explore/台北市/list/%E7%B4%84%E6%9C%83%E9%A4%90%E5%BB%B3%E9%A1%9E', 'https://ifoodie.tw/explore/台北市/list/%E9%9F%93%E5%BC%8F', 'https://ifoodie.tw/explore/台北市/list/%E9%A4%90%E9%85%92%E9%A4%A8%2F%E9%85%92%E5%90%A7', 'https://ifoodie.tw/explore/台北市/list/%E5%B1%85%E9%85%92%E5%B1%8B']


In [8]:
target_hrefs_3 = []

outer_div = soup.find('div', class_='jsx-1638812939 category-block-item-outer')
links = outer_div.findAll('a')

total = 0
for link in links:
    href_2 = link.get('href')
    href_url = f'https://ifoodie.tw{href_2}'
    href_url = href_url.replace('台北市/', '')    # 預設是'台北市', 拿掉
    href_url += '?sortby=popular'                 # 預設是'最新餐廳', 改成'最高人氣'餐廳, URL加上"?sortby=popular"
    target_hrefs_3.append(href_url)
    total += 1
    
    if total == 10:
        break

print(target_hrefs_3)


['https://ifoodie.tw/explore/list/%E9%8D%8B%E9%A1%9E?sortby=popular', 'https://ifoodie.tw/explore/list/%E6%97%A5%E5%BC%8F?sortby=popular', 'https://ifoodie.tw/explore/list/%E7%87%92%E8%82%89?sortby=popular', 'https://ifoodie.tw/explore/list/%E7%B2%BE%E7%B7%BB%E9%AB%98%E7%B4%9A?sortby=popular', 'https://ifoodie.tw/explore/list/%E6%97%A9%E5%8D%88%E9%A4%90?sortby=popular', 'https://ifoodie.tw/explore/list/%E7%94%9C%E9%BB%9E%E9%A1%9E?sortby=popular', 'https://ifoodie.tw/explore/list/%E7%B4%84%E6%9C%83%E9%A4%90%E5%BB%B3%E9%A1%9E?sortby=popular', 'https://ifoodie.tw/explore/list/%E9%9F%93%E5%BC%8F?sortby=popular', 'https://ifoodie.tw/explore/list/%E9%A4%90%E9%85%92%E9%A4%A8%2F%E9%85%92%E5%90%A7?sortby=popular', 'https://ifoodie.tw/explore/list/%E5%B1%85%E9%85%92%E5%B1%8B?sortby=popular']


In [19]:
# 取出 '最高人氣' 第一頁的餐廳資料, 並寫進 mysql

# Connect to the MySQL database
cnx = pymysql.connect(
    host='localhost',
    user='root',
    password='000000',
    database='ifoodie'
)

# Create a cursor object
cursor = cnx.cursor()

# Define the SQL statement
sql = "INSERT INTO ifoodie_v1 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"

# Iterate over the data and execute the SQL statement for each entry
for url in target_hrefs_2:
    response = requests.get(url)
    soup = BeautifulSoup(response.text, "html.parser")
    
    title_div = soup.find('div', class_='jsx-2554500804 query-container')
    title_text = title_div.find('h1', class_='jsx-2554500804 query-title extra-small').div.text
    print(title_text)
    print()
    
    all_blocks = soup.findAll('div', class_='jsx-1156793088 restaurant-info')

    for block in all_blocks:
        restaurant_link = block.find('a', class_='jsx-1156793088')
        
        # restaurant_url
        if restaurant_link:
            restaurant_href = restaurant_link['href']
            restaurant_url = f'https://ifoodie.tw{restaurant_href}'
            print(restaurant_url)

            # restaurant_name
            name = block.find('a', class_='jsx-1156793088 title-text').text
            print(name)

            # address
            addr = block.find('div', class_='jsx-1156793088 address-row').text
            print(addr)

            # all_categories
            category_row = block.find('div', class_='jsx-1156793088 category-row')

            # category.tag
            categories = category_row.find_all('a', class_='jsx-1156793088 category')
            tags = [category.text for category in categories]
            print(tags)
            print()
        else:
            continue

    # Execute the SQL statement with the data
    data = (restaurant_url, name, addr, str(tags))
    cursor.execute(sql, data)

# Commit the changes to the database
cnx.commit()

# Close the cursor and the database connection
cursor.close()
cnx.close()


In [26]:
# 取出 '最高人氣' p1~2 的餐廳資料, 並寫進 mysql
import csv
import pymysql
import requests
from bs4 import BeautifulSoup

# Connect to the MySQL database
cnx = pymysql.connect(
    host='localhost',
    user='root',
    password='000000',
    database='ifoodie'
)

# Create a cursor object
cursor = cnx.cursor()

# Define the SQL statement
sql = "INSERT INTO ifoodie_v1 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"


# Iterate over the data and execute the SQL statement for each entry
for url in target_hrefs_3:
    for page in range(1, 3):  # p1~2
        page_url = f"{url}&page={page}"
        response = requests.get(page_url)
        soup = BeautifulSoup(response.text, "html.parser")

        title_div = soup.find('div', class_='jsx-2554500804 query-container')
        title_text = title_div.find('h1', class_='jsx-2554500804 query-title extra-small').div.text
        print(title_text)
        print()

        all_blocks = soup.findAll('div', class_='jsx-1156793088 restaurant-info')

        for block in all_blocks:
            restaurant_link = block.find('a', class_='jsx-1156793088')

            if restaurant_link:
                restaurant_href = restaurant_link['href']
                restaurant_url = f'https://ifoodie.tw{restaurant_href}'
                print(restaurant_url)

                name = block.find('a', class_='jsx-1156793088 title-text').text
                print(name)

                addr = block.find('div', class_='jsx-1156793088 address-row').text
                print(addr)

                category_row = block.find('div', class_='jsx-1156793088 category-row')
                categories = category_row.find_all('a', class_='jsx-1156793088 category')
                tags = [category.text for category in categories]
                print(tags)
                print()

                # Execute the SQL statement with the data
                data = (restaurant_url, name, addr, str(tags))
                cursor.execute(sql, data)
            else:
                continue
                
# Commit the changes to the database
cnx.commit()

# Close the cursor and the database connection
cursor.close()
cnx.close()

台灣『鍋類餐廳』 | 精選TOP 15間熱門店家

https://ifoodie.tw/restaurant/559c0989c03a101f6d8b7eb0-%E7%9A%87%E5%AE%B6%E5%B8%9D%E5%9C%8B%E9%BA%BB%E8%BE%A3%E7%81%AB%E9%8D%8B
皇家帝國麻辣火鍋
臺北市萬華區中華路一段192號
['附近餐廳', '火鍋', '精緻高級', '約會餐廳', '宵夜']

https://ifoodie.tw/restaurant/5598e9a940b5e30f5545f3d9-%E7%A2%B3%E4%BD%90%E9%BA%BB%E9%87%8C-%E5%BA%9C%E5%89%8D%E5%BA%97
碳佐麻里 府前店
臺南市安平區府前路二段630號
['附近餐廳', '燒烤', '日本料理', '約會餐廳', '小吃']

https://ifoodie.tw/restaurant/603b4690873d7901d4aa8160-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E4%B8%AD%E6%96%87%E5%BF%83%E5%B4%87%E5%BE%B7%E5%BA%97
和牛涮 日式鍋物放題 台中文心崇德店
臺中市北屯區文心路四段601號
['附近餐廳', '火鍋', '日本料理', '咖哩', '精緻高級']

https://ifoodie.tw/restaurant/5e40c1d58c906d27c8497a08-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E5%8C%97%E5%BF%A0%E5%AD%9D%E6%9D%B1%E5%BA%97
和牛涮 日式鍋物放題 台北忠孝東店
臺北市大安區忠孝東路四段128號2樓
['附近餐廳', '火鍋', '約會餐廳', '精緻高級', '午餐']

https://ifoodie.tw/restaurant/56438a032756dd40eaa06178-%E

In [21]:
# 取出 '所有' 種類 all pages 的餐廳資料, 並寫進 mysql
import csv
import pymysql
import requests
from bs4 import BeautifulSoup

# Connect to the MySQL database
cnx = pymysql.connect(
    host='localhost',
    user='root',
    password='000000',
    database='ifoodie'
)

# Create a cursor object
cursor = cnx.cursor()

# Define the SQL statement
sql = "INSERT INTO ifoodie_v1 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"

# Create a list to store the data
data_list = []

# Iterate over the data and execute the SQL statement for each entry
for url in target_hrefs_3:
    response = requests.get(url)
    html_content = response.content

    soup = BeautifulSoup(html_content, 'html.parser')

    search_condition_div = soup.find('div', class_='jsx-987803290 search-condition')
    if search_condition_div is not None:
        last_li = search_condition_div.find_all('li')[-2]
        page_number = int(last_li.text)
        print(page_number)
    else:
        print("Search condition div not found.")


    for page in range(1, page_number + 1):
        page_url = f"{url}&page={page}"
        response = requests.get(page_url)
        soup = BeautifulSoup(response.text, "html.parser")

        title_div = soup.find('div', class_='jsx-2554500804 query-container')
        title_text = title_div.find('h1', class_='jsx-2554500804 query-title extra-small').div.text
        print(title_text)
        print()

        all_blocks = soup.findAll('div', class_='jsx-1156793088 restaurant-info')

        for block in all_blocks:
            restaurant_link = block.find('a', class_='jsx-1156793088')

            if restaurant_link:
                restaurant_href = restaurant_link['href']
                restaurant_url = f'https://ifoodie.tw{restaurant_href}'
                print(restaurant_url)

                name = block.find('a', class_='jsx-1156793088 title-text').text
                print(name)

                addr = block.find('div', class_='jsx-1156793088 address-row').text
                print(addr)

                category_row = block.find('div', class_='jsx-1156793088 category-row')
                categories = category_row.find_all('a', class_='jsx-1156793088 category')
                tags = [category.text for category in categories]
                print(tags)

                print()
                # Append the data to the list
                data_list.append((restaurant_url, name, addr, str(tags)))

# Execute the SQL statement with the data
cursor.executemany(sql, data_list)

# Commit the changes to the database
cnx.commit()

# Close the cursor and the database connection
cursor.close()
cnx.close()


67
台灣『鍋類餐廳』 | 精選TOP 15間熱門店家

https://ifoodie.tw/restaurant/559c0989c03a101f6d8b7eb0-%E7%9A%87%E5%AE%B6%E5%B8%9D%E5%9C%8B%E9%BA%BB%E8%BE%A3%E7%81%AB%E9%8D%8B
皇家帝國麻辣火鍋
臺北市萬華區中華路一段192號
['附近餐廳', '火鍋', '精緻高級', '約會餐廳', '宵夜']

https://ifoodie.tw/restaurant/5598e9a940b5e30f5545f3d9-%E7%A2%B3%E4%BD%90%E9%BA%BB%E9%87%8C-%E5%BA%9C%E5%89%8D%E5%BA%97
碳佐麻里 府前店
臺南市安平區府前路二段630號
['附近餐廳', '燒烤', '日本料理', '約會餐廳', '小吃']

https://ifoodie.tw/restaurant/603b4690873d7901d4aa8160-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E4%B8%AD%E6%96%87%E5%BF%83%E5%B4%87%E5%BE%B7%E5%BA%97
和牛涮 日式鍋物放題 台中文心崇德店
臺中市北屯區文心路四段601號
['附近餐廳', '火鍋', '日本料理', '咖哩', '精緻高級']

https://ifoodie.tw/restaurant/5e40c1d58c906d27c8497a08-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E5%8C%97%E5%BF%A0%E5%AD%9D%E6%9D%B1%E5%BA%97
和牛涮 日式鍋物放題 台北忠孝東店
臺北市大安區忠孝東路四段128號2樓
['附近餐廳', '火鍋', '約會餐廳', '精緻高級', '午餐']

https://ifoodie.tw/restaurant/56438a032756dd40eaa06178

In [9]:
# 取出 '所有' 種類 all pages 的餐廳資料, 並寫進 mysql+csv

import csv
import pymysql
import requests
from bs4 import BeautifulSoup

# Connect to the MySQL database
cnx = pymysql.connect(
    host='localhost',
    user='root',
    password='000000',
    database='ifoodie'
)

# Create a cursor object
cursor = cnx.cursor()

# Define the SQL statement
sql = "INSERT INTO ifoodie_v1 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"

# Create a list to store the data
data_list = []

# Iterate over the data and execute the SQL statement for each entry
for url in target_hrefs_3:
    response = requests.get(url)
    html_content = response.content

    soup = BeautifulSoup(html_content, 'html.parser')

    search_condition_div = soup.find('div', class_='jsx-987803290 search-condition')
    if search_condition_div is not None:
        last_li = search_condition_div.find_all('li')[-2]
        page_number = int(last_li.text)
        print(page_number)
    else:
        print("Search condition div not found.")

    for page in range(1, page_number + 1):
        page_url = f"{url}&page={page}"
        response = requests.get(page_url)
        soup = BeautifulSoup(response.text, "html.parser")

        title_div = soup.find('div', class_='jsx-2554500804 query-container')
        title_text = title_div.find('h1', class_='jsx-2554500804 query-title extra-small').div.text
        print(title_text)
        print()

        all_blocks = soup.findAll('div', class_='jsx-1156793088 restaurant-info')

        for block in all_blocks:
            restaurant_link = block.find('a', class_='jsx-1156793088')

            if restaurant_link:
                restaurant_href = restaurant_link['href']
                restaurant_url = f'https://ifoodie.tw{restaurant_href}'
                print(restaurant_url)

                name = block.find('a', class_='jsx-1156793088 title-text').text
                print(name)

                addr = block.find('div', class_='jsx-1156793088 address-row').text
                print(addr)

                category_row = block.find('div', class_='jsx-1156793088 category-row')
                categories = category_row.find_all('a', class_='jsx-1156793088 category')
                tags = [category.text for category in categories]
                print(tags)

                print()
                # Append the data to the list
                data_list.append((restaurant_url, name, addr, str(tags)))

# Write data to CSV file
csv_file_path = 'restaurant_data.csv'
with open(csv_file_path, 'w', newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['Restaurant URL', 'Restaurant Name', 'Address', 'Category Tags'])
    writer.writerows(data_list)

# Execute the SQL statement with the data
cursor.executemany(sql, data_list)

# Commit the changes to the database
cnx.commit()

# Close the cursor and the database connection
cursor.close()
cnx.close()


67
台灣『鍋類餐廳』 | 精選TOP 15間熱門店家

https://ifoodie.tw/restaurant/559c0989c03a101f6d8b7eb0-%E7%9A%87%E5%AE%B6%E5%B8%9D%E5%9C%8B%E9%BA%BB%E8%BE%A3%E7%81%AB%E9%8D%8B
皇家帝國麻辣火鍋
臺北市萬華區中華路一段192號
['附近餐廳', '火鍋', '精緻高級', '約會餐廳', '宵夜']

https://ifoodie.tw/restaurant/5598e9a940b5e30f5545f3d9-%E7%A2%B3%E4%BD%90%E9%BA%BB%E9%87%8C-%E5%BA%9C%E5%89%8D%E5%BA%97
碳佐麻里 府前店
臺南市安平區府前路二段630號
['附近餐廳', '燒烤', '日本料理', '約會餐廳', '小吃']

https://ifoodie.tw/restaurant/603b4690873d7901d4aa8160-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E4%B8%AD%E6%96%87%E5%BF%83%E5%B4%87%E5%BE%B7%E5%BA%97
和牛涮 日式鍋物放題 台中文心崇德店
臺中市北屯區文心路四段601號
['附近餐廳', '火鍋', '日本料理', '咖哩', '精緻高級']

https://ifoodie.tw/restaurant/5e40c1d58c906d27c8497a08-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E5%8C%97%E5%BF%A0%E5%AD%9D%E6%9D%B1%E5%BA%97
和牛涮 日式鍋物放題 台北忠孝東店
臺北市大安區忠孝東路四段128號2樓
['附近餐廳', '火鍋', '約會餐廳', '精緻高級', '午餐']

https://ifoodie.tw/restaurant/56438a032756dd40eaa06178

In [23]:
# 取出 '所有' 種類 all pages 的餐廳資料, 並寫進 mysql
# 每5000筆一張table, 改成5001~10000 v2 、10001~15000 v3 

import csv
import pymysql
import requests
from bs4 import BeautifulSoup

# Connect to the MySQL database
cnx = pymysql.connect(
    host='localhost',
    user='root',
    password='000000',
    database='ifoodie'
)

# Create a cursor object
cursor = cnx.cursor()

# Define the SQL statements
sql_v1 = "INSERT INTO ifoodie_v1 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"
sql_v2 = "INSERT INTO ifoodie_v2 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"
sql_v3 = "INSERT INTO ifoodie_v3 (restaurant_url, restaurant_name, address, category_tag) VALUES (%s, %s, %s, %s)"

# Create lists to store the data
data_list_v1 = []
data_list_v2 = []
data_list_v3 = []

# Count the number of records
record_count = 0

# Iterate over the data and execute the SQL statement for each entry
for url in target_hrefs_3:
    response = requests.get(url)
    html_content = response.content

    soup = BeautifulSoup(html_content, 'html.parser')

    search_condition_div = soup.find('div', class_='jsx-987803290 search-condition')
    if search_condition_div is not None:
        last_li = search_condition_div.find_all('li')[-2]
        page_number = int(last_li.text)
        print(page_number)
    else:
        print("Search condition div not found.")

    for page in range(1, page_number + 1):
        page_url = f"{url}&page={page}"
        response = requests.get(page_url)
        soup = BeautifulSoup(response.text, "html.parser")

        title_div = soup.find('div', class_='jsx-2554500804 query-container')
        title_text = title_div.find('h1', class_='jsx-2554500804 query-title extra-small').div.text
        print(title_text)
        print()

        all_blocks = soup.findAll('div', class_='jsx-1156793088 restaurant-info')

        for block in all_blocks:
            restaurant_link = block.find('a', class_='jsx-1156793088')

            if restaurant_link:
                restaurant_href = restaurant_link['href']
                restaurant_url = f'https://ifoodie.tw{restaurant_href}'
                print(restaurant_url)

                name = block.find('a', class_='jsx-1156793088 title-text').text
                print(name)

                addr = block.find('div', class_='jsx-1156793088 address-row').text
                print(addr)

                category_row = block.find('div', class_='jsx-1156793088 category-row')
                categories = category_row.find_all('a', class_='jsx-1156793088 category')
                tags = [category.text for category in categories]
                print(tags)

                print()
                # Append the data to the respective list based on the record count
                if record_count < 5000:
                    data_list_v1.append((restaurant_url, name, addr, str(tags)))
                elif record_count < 10000:
                    data_list_v2.append((restaurant_url, name, addr, str(tags)))
                else:
                    data_list_v3.append((restaurant_url, name, addr, str(tags)))

                record_count += 1

                # Check if 5000 records have been reached
                if record_count == 5000:
                    # Execute the SQL statement with the data for ifoodie_v1
                    cursor.executemany(sql_v1, data_list_v1)

                    # Commit the changes to the database for ifoodie_v1
                    cnx.commit()

                    # Clear the data list for ifoodie_v1
                    data_list_v1 = []

                # Check if 10000 records have been reached
                if record_count == 10000:
                    # Execute the SQL statement with the data for ifoodie_v2
                    cursor.executemany(sql_v2, data_list_v2)

                    # Commit the changes to the database for ifoodie_v2
                    cnx.commit()

                    # Clear the data list for ifoodie_v2
                    data_list_v2 = []

                # Check if 15000 records have been reached
                if record_count == 15000:
                    # Execute the SQL statement with the data for ifoodie_v3
                    cursor.executemany(sql_v3, data_list_v3)

                    # Commit the changes to the database for ifoodie_v3
                    cnx.commit()

                    # Clear the data list for ifoodie_v3
                    data_list_v3 = []

# Execute the remaining data for ifoodie_v1
if data_list_v1:
    cursor.executemany(sql_v1, data_list_v1)
    cnx.commit()

# Execute the remaining data for ifoodie_v2
if data_list_v2:
    cursor.executemany(sql_v2, data_list_v2)
    cnx.commit()

# Execute the remaining data for ifoodie_v3
if data_list_v3:
    cursor.executemany(sql_v3, data_list_v3)
    cnx.commit()

# Close the cursor and the database connection
cursor.close()
cnx.close()


67
台灣『鍋類餐廳』 | 精選TOP 15間熱門店家

https://ifoodie.tw/restaurant/559c0989c03a101f6d8b7eb0-%E7%9A%87%E5%AE%B6%E5%B8%9D%E5%9C%8B%E9%BA%BB%E8%BE%A3%E7%81%AB%E9%8D%8B
皇家帝國麻辣火鍋
臺北市萬華區中華路一段192號
['附近餐廳', '火鍋', '精緻高級', '約會餐廳', '宵夜']

https://ifoodie.tw/restaurant/5598e9a940b5e30f5545f3d9-%E7%A2%B3%E4%BD%90%E9%BA%BB%E9%87%8C-%E5%BA%9C%E5%89%8D%E5%BA%97
碳佐麻里 府前店
臺南市安平區府前路二段630號
['附近餐廳', '燒烤', '日本料理', '約會餐廳', '小吃']

https://ifoodie.tw/restaurant/603b4690873d7901d4aa8160-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E4%B8%AD%E6%96%87%E5%BF%83%E5%B4%87%E5%BE%B7%E5%BA%97
和牛涮 日式鍋物放題 台中文心崇德店
臺中市北屯區文心路四段601號
['附近餐廳', '火鍋', '日本料理', '咖哩', '精緻高級']

https://ifoodie.tw/restaurant/5e40c1d58c906d27c8497a08-%E5%92%8C%E7%89%9B%E6%B6%AE-%E6%97%A5%E5%BC%8F%E9%8D%8B%E7%89%A9%E6%94%BE%E9%A1%8C-%E5%8F%B0%E5%8C%97%E5%BF%A0%E5%AD%9D%E6%9D%B1%E5%BA%97
和牛涮 日式鍋物放題 台北忠孝東店
臺北市大安區忠孝東路四段128號2樓
['附近餐廳', '火鍋', '約會餐廳', '精緻高級', '午餐']

https://ifoodie.tw/restaurant/56438a032756dd40eaa06178